# Data Collection - News Sites
So, Brian Jezreel A. DATASCI S12

In [1]:
import requests
from bs4 import BeautifulSoup
import json
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time
PATH = 'C:\Program Files (x86)\chromedriver.exe'

## News Site

In [2]:
driver = webdriver.Chrome(PATH)
driver.get("https://www.nytimes.com/search?dropmab=true&endDate=20210312&query=&sort=best&startDate=20210311")
print(driver.title)

more = False
try:
    showMore = WebDriverWait(driver, 10).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, ".css-vsuiox button"))
    )
    more = True
except:
    print("could not find SHOW MORE")

while(more):
    try:
        showMore = WebDriverWait(driver, 10).until(
            EC.presence_of_element_located((By.CSS_SELECTOR, ".css-vsuiox button"))
        )
        showMore.click()
    except:
        more = False
    time.sleep(0.5)

    
pageSource = driver.page_source
print("DONE CLICKING SHOW MORE")

The New York Times - Search
DONE CLICKING SHOW MORE


In [3]:
soup = BeautifulSoup(pageSource, 'html.parser')
driver.quit()
searchResults = soup.find_all("li", {"class": "css-1l4w6pd"})
len(searchResults)

948

In [4]:
# date = div > span > text
# title = div div div a h4
# full article = div div div a p
# author = div div div a p

div1Contents = searchResults[0].contents[0].contents
print(div1Contents[0].text)
aContents = div1Contents[1].contents[0].contents[1].contents
print(aContents[0].text)
print(aContents[1].text)
print(aContents[2].text.strip('By '))

March11to12Articles = []
for i in range(len(searchResults)):
    print('Processing article ', i)
    div1Contents = searchResults[i].contents[0].contents
    aContents = div1Contents[1].contents[0].contents[1].contents
    
    if(div1Contents[0].text != 'March 11' and div1Contents[0].text != 'March 12'):
        continue
        
    date = div1Contents[0].text.strip()
    title = aContents[0].text.strip()
    fullarticle = aContents[1].text.strip()
    try: 
        href = 'https://www.nytimes.com' + div1Contents[1].contents[0].contents[1]["href"]
        article = requests.get(href)
        subsoup = BeautifulSoup(article.content, 'html.parser')
        allP = subsoup.find_all('p')
        fullarticle = ''
        for p in allP:
            text = p.text.strip()
            if(text == 'Advertisement' or text == 'Supported by' or text == 'letters' or text == 'transcript'):
                continue
            fullarticle+= ' '+text
        fullarticle = fullarticle.strip()
    except KeyError:
        href = "N/A"
    try:
        author = aContents[2].text.strip()
        if(author.startswith('PRINT EDITION')):
            author = "N/A"
    except IndexError:
        author = "N/A"
        
    March11to12Articles.append({
        "date": date,
        "title": title,
        "fullarticle": fullarticle,
        "author": author,
        "href": href
    })

print('Finished parsing '+str(len(searchResults))+' articles')
March11to12Articles

March 12
As Cleveland Searches for a Name, a Fan Roots for His Trademark
Arlen Love applied for the Cleveland Spiders trademark. The Cleveland sports fan insists it is about love, not profit potential.
James Wagner
Processing article  0
Processing article  1
Processing article  2
Processing article  3
Processing article  4
Processing article  5
Processing article  6
Processing article  7
Processing article  8
Processing article  9
Processing article  10
Processing article  11
Processing article  12
Processing article  13
Processing article  14
Processing article  15
Processing article  16
Processing article  17
Processing article  18
Processing article  19
Processing article  20
Processing article  21
Processing article  22
Processing article  23
Processing article  24
Processing article  25
Processing article  26
Processing article  27
Processing article  28
Processing article  29
Processing article  30
Processing article  31
Processing article  32
Processing article  33
Processing ar

Processing article  337
Processing article  338
Processing article  339
Processing article  340
Processing article  341
Processing article  342
Processing article  343
Processing article  344
Processing article  345
Processing article  346
Processing article  347
Processing article  348
Processing article  349
Processing article  350
Processing article  351
Processing article  352
Processing article  353
Processing article  354
Processing article  355
Processing article  356
Processing article  357
Processing article  358
Processing article  359
Processing article  360
Processing article  361
Processing article  362
Processing article  363
Processing article  364
Processing article  365
Processing article  366
Processing article  367
Processing article  368
Processing article  369
Processing article  370
Processing article  371
Processing article  372
Processing article  373
Processing article  374
Processing article  375
Processing article  376
Processing article  377
Processing artic

Processing article  679
Processing article  680
Processing article  681
Processing article  682
Processing article  683
Processing article  684
Processing article  685
Processing article  686
Processing article  687
Processing article  688
Processing article  689
Processing article  690
Processing article  691
Processing article  692
Processing article  693
Processing article  694
Processing article  695
Processing article  696
Processing article  697
Processing article  698
Processing article  699
Processing article  700
Processing article  701
Processing article  702
Processing article  703
Processing article  704
Processing article  705
Processing article  706
Processing article  707
Processing article  708
Processing article  709
Processing article  710
Processing article  711
Processing article  712
Processing article  713
Processing article  714
Processing article  715
Processing article  716
Processing article  717
Processing article  718
Processing article  719
Processing artic

[{'date': 'March 12',
  'title': 'As Cleveland Searches for a Name, a Fan Roots for His Trademark',
  'fullarticle': 'Arlen Love applied for the Cleveland Spiders trademark. The Cleveland sports fan insists it is about love, not profit potential. By James Wagner After decades of resisting calls to change their name, the Cleveland Indians announced last July that they would discuss the future of their moniker in the wake of intensified calls for social reform throughout the country. Five months later, the team went a step further, saying it would drop the name it has used since 1915, beginning as soon as the 2022 season. Within days of the initial summer announcement, the United States Patent and Trademark Office received several trademark filings for potential new names. Among them was an early favorite option among oddsmakers: the Cleveland Spiders. But the request didn’t come from anyone representing the baseball team. Instead, the application was submitted by a man who lives in a su

In [5]:
filename = 'March11to12NYTimesNews.json'
with open(filename, 'w') as outfile:
        json.dump(March11to12Articles, outfile)